In [1]:
!pip install wikiextractor beautifulsoup4

In [2]:
%reload_ext autoreload
%autoreload 2

In [3]:
import re
import requests
from pathlib import Path
import bz2, shutil
from wikiextractor import WikiExtractor
from tqdm import tqdm
from bs4 import BeautifulSoup
import json

In [4]:
WIKI_URL = 'https://dumps.wikimedia.org'

In [5]:
def get_releases(lang: str) -> str:
    
    response = requests.get(f'{WIKI_URL}/ptwiki/')

    if response.status_code != 200:
        raise Exception(f'Status code: {response.status_code}!')
    
    return response.text

In [6]:
def extract_links(html: str) -> list:
       
    soup = BeautifulSoup(html, 'html.parser')
    
    links = soup.find_all('a')

    exclude = ['../', 'latest/']
    
    return [ link.text[:-1] for link in links if link.text not in exclude ]

In [7]:
lang = 'pt'
data_path = Path('./')
directory = data_path / lang
directory.mkdir(exist_ok=True, parents=True)

In [8]:
html = get_releases(lang)
links = extract_links(html)
latest_release = links[-1]
print(f'Latest release: {latest_release}')

Latest release: 20231001


In [9]:
def download_url(url: str, dest: Path) -> None:
    response = requests.get(url)
    dest.write_bytes(response.content)

In [10]:
def unzip_bz2(path_in, path_out):
    with bz2.BZ2File(path_in) as fin:
        with open(path_out, 'wb') as fout:
            shutil.copyfileobj(fin, fout)

In [13]:
def get_wiki(directory: Path, release: str, lang: str) -> Path:
    
    name = f'{lang}wiki'
    
    xml_name = f'{name}-{release}-pages-articles.xml'
    zip_name = f'{xml_name}.bz2'
    
    zip_path = directory / zip_name
    xml_path = directory / xml_name
    
    xml_extracted_path = directory / f'{name}-{release}-pages-articles.extracted.xml'
        
    if not zip_path.exists():
        print(' - Downloading...')
        download_url(f'{WIKI_URL}/{name}/{release}/{zip_name}', zip_path)
    
    if not xml_path.exists():
        print(' - Unzipping...')
        unzip_bz2(zip_path, xml_path)

    zip_path.unlink()
    
    print(' - Extracting...')
    !python3 -m wikiextractor.WikiExtractor --processes 10 --no-templates -b 100G {str(xml_path)} -o {str(directory)}

    shutil.move(str(directory / 'AA/wiki_00'), str(xml_extracted_path))
    shutil.rmtree(directory / 'AA')
    xml_path.unlink()
    print(' - Extract finished...')

    return xml_extracted_path

In [14]:
extracted_path = get_wiki(directory, latest_release, lang)

 - Downloading...
 - Extracting...
INFO: Starting page extraction from pt/ptwiki-20231001-pages-articles.xml.
INFO: Using 10 extract processes.
INFO: Extracted 100000 articles (4618.3 art/s)
INFO: Extracted 200000 articles (7249.8 art/s)
INFO: Extracted 300000 articles (8652.6 art/s)
INFO: Extracted 400000 articles (8658.4 art/s)
INFO: Extracted 500000 articles (9689.9 art/s)
INFO: Extracted 600000 articles (10589.4 art/s)
INFO: Extracted 700000 articles (9007.0 art/s)
INFO: Extracted 800000 articles (9678.8 art/s)
INFO: Extracted 900000 articles (11117.8 art/s)
INFO: Extracted 1000000 articles (9135.0 art/s)
INFO: Extracted 1100000 articles (9356.9 art/s)
INFO: Extracted 1200000 articles (9606.3 art/s)
INFO: Extracted 1300000 articles (9631.8 art/s)
INFO: Extracted 1400000 articles (9716.9 art/s)
INFO: Extracted 1500000 articles (9255.8 art/s)
INFO: Extracted 1600000 articles (8879.2 art/s)
INFO: Extracted 1700000 articles (7984.6 art/s)
INFO: Extracted 1800000 articles (8597.0 art/s)

In [15]:
extracted_path

PosixPath('pt/ptwiki-20231001-pages-articles.extracted.xml')

In [16]:
!head -n90 { extracted_path }

<doc id="220" url="https://pt.wikipedia.org/wiki?curid=220" title="Astronomia">
Astronomia

Astronomia é uma ciência natural que estuda corpos celestes (como estrelas, planetas, cometas, nebulosas, aglomerados de estrelas, galáxias) e fenômenos que se originam fora da atmosfera da Terra (como a radiação cósmica de fundo em micro-ondas). Preocupada com a evolução, a física e a química de objetos celestes, bem como a formação e o desenvolvimento do universo.
A astronomia é uma das mais antigas ciências. Culturas pré-históricas deixaram registrados vários artefatos astronômicos, como Stonehenge, os montes de Newgrange e os menires. As primeiras civilizações, como os babilônios, gregos, chineses, indianos, persas e maias realizaram observações metódicas do céu noturno. No entanto, a invenção do telescópio permitiu o desenvolvimento da astronomia moderna. Historicamente, a astronomia incluiu disciplinas tão diversas como astrometria, navegação astronômica, astronomia observacional e a elabo

## Uploading

In [17]:
!pip install huggingface_hub

In [18]:
import huggingface_hub
from huggingface_hub import notebook_login
from datasets import Dataset, load_dataset

In [19]:
# Huggingface hub authentication
notebook_login(True, True)

In [20]:
def extract_documents(extracted_path: Path, lang: str) -> None:
        
    DOC_RE = re.compile(rf'<doc id="(\d+)" url="https://{lang}.wikipedia.org/wiki\?curid=\d+" title="([^"]+)">')

    directory.mkdir(exist_ok=True, parents=True)
    
    fin = extracted_path.open()
    
    document = None
    
    for line in fin:
        
        if line.startswith('<doc id="'):            
            
            matches = DOC_RE.findall(line)

            id = matches[0][0]
            title = matches[0][1].replace('/','_')
            
            document = {
                'id': id,
                'title': title
            }
            
            content = []
            
        elif '</doc>\n' in line:
            document['text'] = ''.join(content)
            yield document
        else:
            content.append(line)

In [21]:
dataset = Dataset.from_generator(extract_documents, gen_kwargs={ 'extracted_path': extracted_path, 'lang': lang })

In [23]:
print(f'Number of documents: {len(dataset)}')

Number of documents: 1857355


In [24]:
print(dataset[0]['id'], ' - ', dataset[0]['title'])
print('-----------------------------------')
print(dataset[0]['text'])

220  -  Astronomia
-----------------------------------
Astronomia

Astronomia é uma ciência natural que estuda corpos celestes (como estrelas, planetas, cometas, nebulosas, aglomerados de estrelas, galáxias) e fenômenos que se originam fora da atmosfera da Terra (como a radiação cósmica de fundo em micro-ondas). Preocupada com a evolução, a física e a química de objetos celestes, bem como a formação e o desenvolvimento do universo.
A astronomia é uma das mais antigas ciências. Culturas pré-históricas deixaram registrados vários artefatos astronômicos, como Stonehenge, os montes de Newgrange e os menires. As primeiras civilizações, como os babilônios, gregos, chineses, indianos, persas e maias realizaram observações metódicas do céu noturno. No entanto, a invenção do telescópio permitiu o desenvolvimento da astronomia moderna. Historicamente, a astronomia incluiu disciplinas tão diversas como astrometria, navegação astronômica, astronomia observacional e a elaboração de calendários. Dur

In [25]:
# Push the dataset to the Hugging Face Hub
repo = f'pablo-moreira/wikipedia-{lang}'

In [27]:
dataset.push_to_hub(repo, latest_release)

Pushing dataset shards to the dataset hub:   0%|          | 0/5 [00:00<?, ?it/s]

In [28]:
dataset.push_to_hub(repo, 'latest')

Pushing dataset shards to the dataset hub:   0%|          | 0/5 [00:00<?, ?it/s]